In [27]:
import pandas as pd
import scipy.constants
from scipy.optimize import curve_fit
from scipy.integrate import quad
from sklearn.metrics import r2_score
import numpy as np
import math
import matplotlib.pyplot as plt
import matplotlib.dates as md
import matplotlib.transforms as transforms
from matplotlib.ticker import LogFormatter
%matplotlib qt
# %matplotlib inline
import datetime as dt
pd.set_option('display.max_rows', 20000) 

## S3 H2 adsorption isotherm, lumped injections

### Reading in the data and preparing DataFrames

In [28]:
#reading vaclogger measurement file
vaclog=pd.read_csv("vaclog", sep="\t")
vaclog.head()

#adding an elapsed time column
vac_timestamps=pd.to_datetime(vaclog["TAime"],format="%d/%m/%Y %H:%M:%S")
runtime=(vac_timestamps-vac_timestamps[0]).dt.total_seconds()    
vaclog.insert(2,"Elapsed time",runtime)
# vaclog.drop(index=vaclog.index[0], 
#         axis=0, 
#         inplace=True)
vaclog["Time"] = vac_timestamps.dt.strftime('%d-%m-%Y %H:%M:%S')
vaclog["Time"] = pd.to_datetime(vaclog["Time"],format='%d-%m-%Y %H:%M:%S')

print(vaclog)

                  Live comments                Time  Elapsed time  \
0                           NaN 2022-12-14 15:09:10           0.0   
1                           NaN 2022-12-14 15:09:17           7.0   
2                           NaN 2022-12-14 15:09:25          15.0   
3                           NaN 2022-12-14 15:09:32          22.0   
4                           NaN 2022-12-14 15:09:39          29.0   
5                           NaN 2022-12-14 15:09:46          36.0   
6                           NaN 2022-12-14 15:09:53          43.0   
7                           NaN 2022-12-14 15:10:00          50.0   
8                           NaN 2022-12-14 15:10:08          58.0   
9                           NaN 2022-12-14 15:10:15          65.0   
10                          NaN 2022-12-14 15:10:22          72.0   
11                          NaN 2022-12-14 15:10:29          79.0   
12                          NaN 2022-12-14 15:10:36          86.0   
13                          NaN 20

## Data processing

In [29]:
#print vaclog comments
print(pd.unique(vaclog["Live comments"]))

[nan 'LHe transfer in progress' 'rinsing inj lines' 'inj volume filled'
 'LHe transfer complete' 'injection started' 'LHe fill started']


#### CernOx temperature R-T conversion

In [30]:
#Temperature curve for CERNOX 
A=[230.317302,-6170.1513,71837.9529,-477946.76,2.003668910085786e+6,-5.488690193047771e+6,9.830475663897528e+6,-1.111226817786569e+7,7.202477878914065e+6,-2.04194551328507e+6]
#specify fit parameters A, data (Resistance values)
def polyfit(params,data):
    total=[]
    for j in data: 
        exp=0
        for i in range(len(params)):
            exp += (params[i]/(math.log10(j))**i)
        total.append(10**exp)
    return(total)    


In [31]:
#Plotting the general pressure evolution for overview
fig, ax = plt.subplots()

l5 = ax.plot(vaclog["Elapsed time"]/3600, polyfit(A,vaclog["T-CERNOX"]),marker=".", color="cyan", markersize=5,label='Temperature')
ax.set_ylabel('Temperature (K)')

ax.set_xlabel('Elapsed time (h)')
ax2=ax.twinx()

l1 = ax2.plot((vaclog["Elapsed time"]/3600),vaclog['Barion_1']/0.46,marker=".", markersize=5,label='BA1')
l2 = ax2.plot((vaclog["Elapsed time"]/3600),vaclog['Barion_2']/0.46,marker=".", markersize=5,label='BA2')
l3 = ax2.plot((vaclog["Elapsed time"]/3600),vaclog['DUAL experiment'],marker=".", markersize=5,label='Dual gauge')
l4 = ax2.plot((vaclog["Elapsed time"]/3600),vaclog['injection 100mbar'],marker=".", markersize=5,label='100mbar F-R')
ax2.set_ylabel('Pressure (mbar)')
#TODO - annotations
font = {'family': 'arial',
        'color':  'green',
        'weight': 'normal',
        'size': 10,
        }
plt.text(14.8, 7.36e-6, 'Pressure rise due to LHe refill \u2192 ', fontdict = font)
plt.text(21, 1e-5, '~Saturated vapor pressure', fontdict = font)
ax2.legend(handles = l1+l2+l3+l4+l5, loc="upper right")
plt.title("Pressure evolution + temperatures. Correction for H2 applied.")
ax2.set_yscale('log')


In [32]:
#slicing the dataset
ramp = vaclog.iloc[list((vaclog["Elapsed time"]/3600).between(1.19,40))]
print(ramp)

           Live comments                Time  Elapsed time  injection 100mbar  \
597                  NaN 2022-12-14 16:20:35        4285.0             96.270   
598                  NaN 2022-12-14 16:20:42        4292.0             96.271   
599                  NaN 2022-12-14 16:20:49        4299.0             96.270   
600                  NaN 2022-12-14 16:20:57        4307.0             96.270   
601                  NaN 2022-12-14 16:21:04        4314.0             96.274   
602                  NaN 2022-12-14 16:21:11        4321.0             96.274   
603                  NaN 2022-12-14 16:21:18        4328.0             96.274   
604                  NaN 2022-12-14 16:21:25        4335.0             96.278   
605                  NaN 2022-12-14 16:21:32        4342.0             96.278   
606                  NaN 2022-12-14 16:21:40        4350.0             96.278   
607                  NaN 2022-12-14 16:21:47        4357.0             96.282   
608                  NaN 202

In [33]:
#plotting the sliced data
#Plotting the general pressure evolution for overview
fig, ax = plt.subplots()

ax.plot((ramp["Elapsed time"]/3600),ramp['Barion_1']/0.46,marker=".", markersize=5,label='BA1')
ax.plot((ramp["Elapsed time"]/3600),ramp['Barion_2']/0.46,marker=".", markersize=5,label='BA2')
ax.plot((ramp["Elapsed time"]/3600),ramp['DUAL experiment'],marker=".", markersize=5,label='DUAL gauge')
plt.legend(loc="upper right")

ax.set_xlabel('Elapsed time (h)')
ax.set_ylabel('Pressure (mbar)')
ax.set_yscale('linear')
font = {'family': 'arial',
        'color':  'green',
        'weight': 'normal',
        'size': 12,
        }
plt.text(14.25, 6e-6, 'Pressure rise due to LHe refill \u2192 ', fontdict = font)
plt.text(13.02, 4.32e-6, 'Temperature fluctuation \u2192', fontdict = font)
plt.legend(loc="upper right")
plt.title("Pressure evolution during injection. Corrected for H2")


Text(0.5, 1.0, 'Pressure evolution during injection. Corrected for H2')

In [34]:
#TODO - calculating coverages for plotting pressure v coverage
#in the first assumption coverage is assumed to be equivalent to the number of molecules injected
#coverage at any given time point in [M/cm2] -> M/s * total injection time 
#First - Determine the inj start point, set elapsed time here to 0. 
inj = vaclog.loc[vaclog["Barion_2"]/0.46 >= 9e-8]
inj.drop(columns="Elapsed time", inplace=True)
print(inj)
timestamps2 = pd.to_datetime(inj["Time"],format="%d/%m/%Y %H:%M:%S")
runtime2 = (timestamps2-timestamps2[633]).dt.total_seconds()    #NB! hardcoded
inj.insert(1,"Elapsed time",runtime2)



C:\Users\etiirine\AppData\Local\Temp\ipykernel_9920\113296010.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  inj.drop(columns="Elapsed time", inplace=True)


          Live comments                Time  injection 100mbar      Barion_2  \
633                 NaN 2022-12-14 16:24:53             96.302  1.550000e-07   
634                 NaN 2022-12-14 16:25:01             96.298  1.680000e-07   
635                 NaN 2022-12-14 16:25:08             96.298  2.340000e-07   
636                 NaN 2022-12-14 16:25:15             96.294  1.040000e-07   
637                 NaN 2022-12-14 16:25:22             96.295  6.830000e-08   
638                 NaN 2022-12-14 16:25:29             96.294  4.160000e-08   
654                 NaN 2022-12-14 16:27:24             96.303  5.530000e-08   
655                 NaN 2022-12-14 16:27:31             96.303  5.910000e-08   
656                 NaN 2022-12-14 16:27:39             96.302  5.930000e-08   
657                 NaN 2022-12-14 16:27:46             96.302  5.930000e-08   
658                 NaN 2022-12-14 16:27:53             96.302  5.950000e-08   
659                 NaN 2022-12-14 16:28

## Subtracting baseline

In [35]:
#TODO - subtract the baseline from graph 2 (linear pressure scale) and plot again
#adding H2 equiv pressure readings
inj.insert(3, "corr BA2", inj["Barion_2"]/0.46)
inj.insert(4, "corr BA1", inj["Barion_1"]/0.46)


### Thermal transpiration
Applied for the gauge readings using the formula below:
    $$
    \frac{p_2}{p_1}=\sqrt \frac{T_2}{T_1}
    $$
Here $p_2$ and $T_2$ are the pressure and temperature in the cold part and $p_1$, $T_1$ are the pressure, temperature the gauge is exposed to.

In [36]:
#implementing the formula
T2 = 4.2
T1 = 293
p_coef = 1#np.sqrt(T2/T1)
inj.insert(3, "H2 4K BA2", (inj["corr BA2"]*p_coef))
inj.insert(4, "H2 4K BA1", (inj["corr BA1"]*p_coef))


In [37]:
print(p_coef)
inj.head()

1


Live comments  Elapsed time                Time     H2 4K BA2  \
633           NaN           0.0 2022-12-14 16:24:53  3.369565e-07   
634           NaN           8.0 2022-12-14 16:25:01  3.652174e-07   
635           NaN          15.0 2022-12-14 16:25:08  5.086957e-07   
636           NaN          22.0 2022-12-14 16:25:15  2.260870e-07   
637           NaN          29.0 2022-12-14 16:25:22  1.484783e-07   

        H2 4K BA1      corr BA2      corr BA1  injection 100mbar  \
633  3.347826e-07  3.369565e-07  3.347826e-07             96.302   
634  3.934783e-07  3.652174e-07  3.934783e-07             96.298   
635  5.021739e-07  5.086957e-07  5.021739e-07             96.298   
636  2.217391e-07  2.260870e-07  2.217391e-07             96.294   
637  1.458696e-07  1.484783e-07  1.458696e-07             96.295   

         Barion_2      Barion_1  DUAL experiment  DUAL insulation  \
633  1.550000e-07  1.540000e-07     1.336000e-07     3.305000e-07   
634  1.680000e-07  1.810000e-07     1.935000e-07     3.309000e-07   
635  2.340000e-07  2.310000e-07     1.139000e-07     3.309000e-07   
636  1.040000e-07  1.020000e-07     7.460000e-08     3.309000e-07   
637  6.830000e-08  6.710000e-08     4.528000e-08     3.309000e-07   

     injection 1mbar  helium  T-platinum  T-CERNOX  I_emission  I_grid  
633              1.1   407.0      -5.050  4281.128         NaN     NaN  
634              1.1   408.0      -5.163  4281.240         NaN     NaN  
635              1.1   408.0      -5.050  4281.240         NaN     NaN  
636              1.1   408.0      -4.938  4281.240         NaN     NaN  
637              1.1   408.0      -5.163  4281.464         NaN     NaN

In [38]:
#define baseline
base1 = inj[inj["corr BA1"].between(1e-7,2e-7)]
base2 = inj[inj["corr BA2"].between(1e-7,2e-7)]

#take the average of the baseline and apply thermal transpiration coef to these values
avg2 = np.mean(base1["corr BA2"])
avg1 = np.mean(base2["corr BA1"])

#subtract the baseline from the graph to get the actual pressure evolution on the sample
base_corr1 = inj['H2 4K BA1'].sub(avg1).clip(lower=0)
base_corr2 = inj['H2 4K BA2'].sub(avg2).clip(lower=0)

#define base pressure
bp1 = np.mean(vaclog["Barion_1"].iloc[:20])
bp2 = np.mean(vaclog["Barion_2"].iloc[:20])
print(bp1)
#add base pressure
base_corr1 = base_corr1.add(bp1)
base_corr2 = base_corr2.add(bp2)

#insert these variables into inj dataframe
inj.insert(3,"Base_p corrected BA1",base_corr1)
inj.insert(4,"Base_p corrected BA2",base_corr2)

inj.head()

9.5735e-10


Live comments  Elapsed time                Time  Base_p corrected BA1  \
633           NaN           0.0 2022-12-14 16:24:53          2.051609e-07   
634           NaN           8.0 2022-12-14 16:25:01          2.638566e-07   
635           NaN          15.0 2022-12-14 16:25:08          3.725522e-07   
636           NaN          22.0 2022-12-14 16:25:15          9.211744e-08   
637           NaN          29.0 2022-12-14 16:25:22          1.624787e-08   

     Base_p corrected BA2     H2 4K BA2     H2 4K BA1      corr BA2  \
633          2.082209e-07  3.369565e-07  3.347826e-07  3.369565e-07   
634          2.364818e-07  3.652174e-07  3.934783e-07  3.652174e-07   
635          3.799601e-07  5.086957e-07  5.021739e-07  5.086957e-07   
636          9.735136e-08  2.260870e-07  2.217391e-07  2.260870e-07   
637          1.974267e-08  1.484783e-07  1.458696e-07  1.484783e-07   

         corr BA1  injection 100mbar      Barion_2      Barion_1  \
633  3.347826e-07             96.302  1.550000e-07  1.540000e-07   
634  3.934783e-07             96.298  1.680000e-07  1.810000e-07   
635  5.021739e-07             96.298  2.340000e-07  2.310000e-07   
636  2.217391e-07             96.294  1.040000e-07  1.020000e-07   
637  1.458696e-07             96.295  6.830000e-08  6.710000e-08   

     DUAL experiment  DUAL insulation  injection 1mbar  helium  T-platinum  \
633     1.336000e-07     3.305000e-07              1.1   407.0      -5.050   
634     1.935000e-07     3.309000e-07              1.1   408.0      -5.163   
635     1.139000e-07     3.309000e-07              1.1   408.0      -5.050   
636     7.460000e-08     3.309000e-07              1.1   408.0      -4.938   
637     4.528000e-08     3.309000e-07              1.1   408.0      -5.163   

     T-CERNOX  I_emission  I_grid  
633  4281.128         NaN     NaN  
634  4281.240         NaN     NaN  
635  4281.240         NaN     NaN  
636  4281.240         NaN     NaN  
637  4281.464         NaN     NaN

In [1]:
#Plotting the h2 equiv base pressure subtracted data
fig, ax = plt.subplots()

ax.plot((inj["Elapsed time"]/3600),inj['H2 4K BA1'],marker=".", markersize=5,label='BA1')
ax.plot((inj["Elapsed time"]/3600),inj['H2 4K BA2'],marker=".", markersize=5,label='BA2')
plt.legend(loc="upper left")

ax.set_xlabel('Elapsed time (h)')
ax.set_ylabel('Pressure (mbar)')
ax.set_yscale('linear')

plt.legend(loc="upper right")
plt.title("Pressure evolution on the sample, p increase from inj flux subtracted. \n Pressures H2 equivalent, thermal transp. corrected ")


NameError: name 'plt' is not defined

### Injection pressure linearity

In [40]:
#defining a function for the straight line
def func(x,a,b):
    return a*x + b
#curve fit for the data
y = inj["injection 100mbar"].values
x = (inj["Elapsed time"]/3600).values
params, cov = curve_fit(func,x,y)
#straight line parameters
a, b = params
print(f"Fitted line: y = {a:.2f}*x+{b:.2f}")

Fitted line: y = -0.30*x+96.47


In [41]:
#checking inj pressure linearity, graph
fig, ax = plt.subplots()
y_fit = func(x,a,b)
ax.plot((inj["Elapsed time"]/3600),inj["injection 100mbar"],marker=".", markersize=5,label='inj volume pressure')
ax.plot((inj["Elapsed time"]/3600),y_fit, "--",color="red", label="Fit") 
ax.legend(loc="upper right")

ax.set_xlabel('Elapsed time (h)')
ax.set_ylabel('Pressure (mbar)')
ax.set_yscale('linear')
plt.title("Injection pressure evolution 100mbar conductance gauge")

Text(0.5, 1.0, 'Injection pressure evolution 100mbar conductance gauge')

### Formula for sum of the differential injection flux
$$
N=\frac{\Sigma dp\cdot V_{inj}}{k_B\cdot T}=\frac{\Sigma (p_{inj,t(x)}-p_{inj,t(x-1)})\cdot V_{inj}}{k_B \cdot T}   \space \left[{M}\right]
$$

In [42]:
#constants in SI units
T = 293
k_B = 1.38e-23
V_inj = 6.515e-5
S_sample= 276
#implement the formula above
dp = abs(np.diff(inj["injection 100mbar"]*100))
print(np.mean(dp))
#dt = np.diff(inj["Elapsed time"])
#dif = abs(dp)*V_inj/dt
dp = np.insert(dp,0,0)
N_x = (dp.cumsum())*V_inj/(k_B*T)
print(N_x)
N_cov = (N_x/S_sample)
print(N_cov)


0.0940838126540632
[0.00000000e+00 6.44507098e+15 6.44507098e+15 ... 1.84490157e+19
 1.84490157e+19 1.84490157e+19]
[0.00000000e+00 2.33517064e+13 2.33517064e+13 ... 6.68442597e+16
 6.68442597e+16 6.68442597e+16]


In [43]:
inj.insert(2, "Coverage",N_cov)


In [44]:
inj.head()

Live comments  Elapsed time      Coverage                Time  \
633           NaN           0.0  0.000000e+00 2022-12-14 16:24:53   
634           NaN           8.0  2.335171e+13 2022-12-14 16:25:01   
635           NaN          15.0  2.335171e+13 2022-12-14 16:25:08   
636           NaN          22.0  4.670341e+13 2022-12-14 16:25:15   
637           NaN          29.0  5.254134e+13 2022-12-14 16:25:22   

     Base_p corrected BA1  Base_p corrected BA2     H2 4K BA2     H2 4K BA1  \
633          2.051609e-07          2.082209e-07  3.369565e-07  3.347826e-07   
634          2.638566e-07          2.364818e-07  3.652174e-07  3.934783e-07   
635          3.725522e-07          3.799601e-07  5.086957e-07  5.021739e-07   
636          9.211744e-08          9.735136e-08  2.260870e-07  2.217391e-07   
637          1.624787e-08          1.974267e-08  1.484783e-07  1.458696e-07   

         corr BA2      corr BA1  ...      Barion_2      Barion_1  \
633  3.369565e-07  3.347826e-07  ...  1.550000e-07  1.540000e-07   
634  3.652174e-07  3.934783e-07  ...  1.680000e-07  1.810000e-07   
635  5.086957e-07  5.021739e-07  ...  2.340000e-07  2.310000e-07   
636  2.260870e-07  2.217391e-07  ...  1.040000e-07  1.020000e-07   
637  1.484783e-07  1.458696e-07  ...  6.830000e-08  6.710000e-08   

     DUAL experiment  DUAL insulation  injection 1mbar  helium  T-platinum  \
633     1.336000e-07     3.305000e-07              1.1   407.0      -5.050   
634     1.935000e-07     3.309000e-07              1.1   408.0      -5.163   
635     1.139000e-07     3.309000e-07              1.1   408.0      -5.050   
636     7.460000e-08     3.309000e-07              1.1   408.0      -4.938   
637     4.528000e-08     3.309000e-07              1.1   408.0      -5.163   

     T-CERNOX  I_emission  I_grid  
633  4281.128         NaN     NaN  
634  4281.240         NaN     NaN  
635  4281.240         NaN     NaN  
636  4281.240         NaN     NaN  
637  4281.464         NaN     NaN  

[5 rows x 21 columns]

## Plotting

In [45]:
#plotting parameters
font = {'family': 'arial',
        'color':  'green',
        'weight': 'normal',
        'size': 10,
        }

plt.rcParams["figure.figsize"] = [8, 5]
plt.rcParams["axes.grid"] = True
plt.rcParams["grid.color"] = "black"
plt.rcParams["grid.linewidth"] = 0.35
plt.rcParams["axes.grid.axis"] = "both"
plt.rcParams["axes.grid.which"] = "both"



In [46]:
#Plotting the general pressure evolution and temperature for overview
#On left y-axis, plot temperature vs time
fig, ax = plt.subplots()

l5 = ax.plot(vaclog["Time"], polyfit(A,vaclog["T-CERNOX"]),marker=".", color="cyan", markersize=5,label='Temperature')
ax.set_ylabel('Temperature (K)')
ax.set_xlabel('Timestamp')

# Format the x-axis as timestamps
ax = plt.gca()
ax.xaxis.set_major_formatter(md.DateFormatter('%H:%M'))
ax.xaxis.set_major_locator(plt.MaxNLocator(12))
for label in ax.get_xticklabels(which='major'):
    label.set(rotation=30, horizontalalignment='right')  

# Rotate and align the x-axis tick labels
fig.autofmt_xdate(rotation=40, ha='right')

#Duplicate x axis for pressure values
ax2=ax.twinx()
l1 = ax2.plot(vaclog["Time"],vaclog["Barion_1"],marker=".", markersize=4,label='Barion 1')
l2 = ax2.plot(vaclog["Time"],vaclog["Barion_2"],marker=".", markersize=4,label='Barion 2')
l3 = ax2.plot(vaclog["Time"],vaclog['DUAL experiment'],marker=".", markersize=4,label='Dual gauge')
l4 = ax2.plot(vaclog["Time"],vaclog['injection 100mbar'],marker=".", markersize=4,label='100mbar F-R')
ax2.xaxis.set_tick_params(which="major",width=1.5, length=3, pad=5)
ax2.set_ylabel('N2 equiv Pressure (mbar)')

ax2.legend(handles = l1+l2+l3+l4+l5, loc="upper right")
plt.title("Pressure evolution + temperatures")
ax2.set_yscale('log')


plt.tight_layout()  # Ensure all elements are properly placed within the figure
plt.savefig(r'./graphs/S4 a-C H2 adsorption isotherm_overview.png', dpi=300)
plt.show()



In [47]:
#Plotting BA2, BA1 pressure
plt.figure(figsize=(12,6))
plt.plot(vaclog["Time"],vaclog["Barion_2"],marker=".", markersize=4,label='Barion 2')
plt.plot(vaclog["Time"],vaclog["Barion_1"],marker=".", markersize=4,label='Barion 1')
plt.plot(vaclog["Time"],vaclog["DUAL experiment"],marker=".", markersize=4,label='DUAL experiment')
plt.plot(vaclog["Time"],vaclog['injection 100mbar'],marker=".", markersize=4,label='100mbar F-R')

plt.xlabel('Timestamp')
plt.ylabel('Pressure (mbar)')
plt.legend()
plt.title("S1 CU ESD sample out - Total pressure evolution")
plt.tick_params(axis="y", which='minor')
plt.grid(which='minor', axis='y')
plt.yscale('log')

ax = plt.gca()
ax.xaxis.set_major_formatter(md.DateFormatter('%H:%M'))
ax.xaxis.set_major_locator(plt.MaxNLocator(12))
for label in ax.get_xticklabels(which='major'):
    label.set(rotation=30, horizontalalignment='right')    
       
plt.tight_layout()  # Ensure all elements are properly placed within the figure
plt.savefig(r'./graphs/S4 a-C H2 adsorption isotherm_Pressures.png',dpi=300)
plt.show()

In [48]:
#plotting the sliced data
#Plotting the general pressure evolution for overview
fig, ax = plt.subplots(figsize=(12,6))

ax.plot(ramp["Time"],ramp['Barion_1'],marker=".", markersize=4,label='BA1')
ax.plot(ramp["Time"],ramp['Barion_2'],marker=".", markersize=4,label='BA2')
ax.plot(ramp["Time"],ramp['DUAL experiment'],marker=".", markersize=4,label='DUAL gauge')

plt.legend(loc="upper right")

ax.set_xlabel('Timestamp')
ax.set_ylabel('H2 equivalent pressure (mbar)')
ax.set_yscale('linear')

plt.text(14.25, 6e-6, 'Pressure rise due to LHe refill \u2192 ', fontdict = font)
plt.text(13.02, 4.32e-6, 'Temperature fluctuation \u2192', fontdict = font)
plt.legend(loc="upper right")
plt.title("Pressure evolution during injection. Corrected for H2")

ax = plt.gca()
ax.xaxis.set_major_formatter(md.DateFormatter('%H:%M'))
ax.xaxis.set_major_locator(plt.MaxNLocator(12))
for label in ax.get_xticklabels(which='major'):
    label.set(rotation=30, horizontalalignment='right')  

plt.tight_layout()  # Ensure all elements are properly placed within the figure       
plt.savefig(r'./graphs/S3 a-C H2 adsorption isotherm_Sliced df Pressures.png',dpi=300)
plt.show()



C:\Users\etiirine\AppData\Local\Temp\ipykernel_9920\696399732.py:26: UserWarning: Tight layout not applied. The left and right margins cannot be made large enough to accommodate all axes decorations.
  plt.tight_layout()  # Ensure all elements are properly placed within the figure


In [49]:
#Plotting coverage vs time
fig, ax = plt.subplots()

ax.plot(inj["Time"],inj["Coverage"],marker=".", markersize=5,label='Coverage')
ax.legend(loc="upper right")

ax.set_xlabel('Elapsed time (h)')
ax.set_ylabel('Coverage (M/cm2)')
ax.set_yscale('linear')
plt.text(15.30, 8e+15, 'Slope change coherent with inj. pressure graph \u2192 ', fontdict = font)
plt.title("Coverage over time")

ax = plt.gca()
ax.xaxis.set_major_formatter(md.DateFormatter('%H:%M'))
ax.xaxis.set_major_locator(plt.MaxNLocator(12))
for label in ax.get_xticklabels(which='major'):
    label.set(rotation=30, horizontalalignment='right')  
    
plt.tight_layout()  # Ensure all elements are properly placed within the figure       
plt.savefig(r'./graphs/S3 a-C H2 ads isotherm_coverage vs time.png',dpi=300)
plt.show()

C:\Users\etiirine\AppData\Local\Temp\ipykernel_9920\856868681.py:19: UserWarning: Tight layout not applied. The left and right margins cannot be made large enough to accommodate all axes decorations.
  plt.tight_layout()  # Ensure all elements are properly placed within the figure


In [50]:
## dropping coverage values close to 0
inj_new = inj.loc[inj['Coverage'] > 1e+13]
inj_new.head()
#inj_new["H2 4K BA2"].sub(avg2).describe()

Live comments  Elapsed time      Coverage                Time  \
634           NaN           8.0  2.335171e+13 2022-12-14 16:25:01   
635           NaN          15.0  2.335171e+13 2022-12-14 16:25:08   
636           NaN          22.0  4.670341e+13 2022-12-14 16:25:15   
637           NaN          29.0  5.254134e+13 2022-12-14 16:25:22   
638           NaN          36.0  5.837927e+13 2022-12-14 16:25:29   

     Base_p corrected BA1  Base_p corrected BA2     H2 4K BA2     H2 4K BA1  \
634          2.638566e-07          2.364818e-07  3.652174e-07  3.934783e-07   
635          3.725522e-07          3.799601e-07  5.086957e-07  5.021739e-07   
636          9.211744e-08          9.735136e-08  2.260870e-07  2.217391e-07   
637          1.624787e-08          1.974267e-08  1.484783e-07  1.458696e-07   
638          9.573500e-10          3.323000e-09  9.043478e-08  8.891304e-08   

         corr BA2      corr BA1  ...      Barion_2      Barion_1  \
634  3.652174e-07  3.934783e-07  ...  1.680000e-07  1.810000e-07   
635  5.086957e-07  5.021739e-07  ...  2.340000e-07  2.310000e-07   
636  2.260870e-07  2.217391e-07  ...  1.040000e-07  1.020000e-07   
637  1.484783e-07  1.458696e-07  ...  6.830000e-08  6.710000e-08   
638  9.043478e-08  8.891304e-08  ...  4.160000e-08  4.090000e-08   

     DUAL experiment  DUAL insulation  injection 1mbar  helium  T-platinum  \
634     1.935000e-07     3.309000e-07              1.1   408.0      -5.163   
635     1.139000e-07     3.309000e-07              1.1   408.0      -5.050   
636     7.460000e-08     3.309000e-07              1.1   408.0      -4.938   
637     4.528000e-08     3.309000e-07              1.1   408.0      -5.163   
638     2.502000e-08     3.309000e-07              1.1   408.0      -5.163   

     T-CERNOX  I_emission  I_grid  
634  4281.240         NaN     NaN  
635  4281.240         NaN     NaN  
636  4281.240         NaN     NaN  
637  4281.464         NaN     NaN  
638  4281.464         NaN     NaN  

[5 rows x 21 columns]

In [51]:
#plotting pressure vs coverage
fig, ax = plt.subplots(linewidth=10)

ax.plot((inj["Coverage"]),inj["Base_p corrected BA2"].sub(avg2),marker=".", markersize=5,label='isotherm')
ax.legend(loc="upper left")
ax.set_xlim(left = 1.4e16,right = 6.65e16)
ax.set_ylim(bottom=1e-9)

ax.set_xlabel('Coverage (M/cm2)')
ax.set_ylabel('H2 equivalent pressure (mbar)')
ax.set_yscale('log')

plt.text(3e+16, 5.2e-6, 'Pressure rise due to LHe refill \u2192 ', fontdict = font)
#plt.text(8.15e+15, 8.7e-7, '~Saturated vapor pressure', fontdict = font)
plt.title("H2 adsorption isotherm")

       
plt.tight_layout()  # Ensure all elements are properly placed within the figure       
plt.savefig(r'./graphs/S3 a-C H2 adsorption isotherm.png',dpi=300)
plt.show()

## Writing dataframes to files

In [52]:
#desorption yield params
#vaclog
vaclog.to_csv(r'./calculated datasets/vaclogger_output.csv', sep='\t', encoding='utf-8', header=True)

#CERNoX
temps_dict = {"Timestamp":vaclog["Time"],"Temperatures":polyfit(A,vaclog["T-CERNOX"])}
temps = pd.DataFrame(temps_dict)
temps.to_csv(r'./calculated datasets/CERNoX temps.csv', sep='\t', encoding='utf-8', header=True)
#coverage
inj.to_csv(r'./calculated datasets/vaclog during injection.csv', sep='\t', encoding='utf-8', header=True)

#coverage > 1e13
inj_new.to_csv(r'./calculated datasets/cut vaclog during injection.csv', sep='\t', encoding='utf-8', header=True)
